In [2]:
import geopandas as gpd
import pandas as pd
import folium
import json

# Load data
data = gpd.read_file('export.geojson')

# Define the cleaning function
def clean_geodataframe(gdf):
    gdf = gdf.reset_index(drop=True)
    cols_needed = ['name', 'amenity', 'building', 'shop', 'tourism', 'leisure', 'geometry']
    for col in cols_needed:
        if col not in gdf.columns:
            gdf[col] = ''
    gdf = gdf[cols_needed]
    for col in cols_needed:
        if col != 'geometry':
            gdf[col] = gdf[col].astype(str)
    # Remove Null geometries
    gdf = gdf[gdf['geometry'].notnull()]
    # Ensure geometries are valid
    gdf['geometry'] = gdf['geometry'].buffer(0)
    return gdf

# Categorize data
residence = data[data['building'].isin(['apartments', 'house', 'residential', 'detached', 'hotel', 'hostel', 'dormitory'])]
office = data[(data['building'].isin(['office', 'industrial', 'warehouse', 'factory', 'commercial'])) | (data['office'].notnull())]
study = data[data['amenity'].isin(['library', 'school', 'kindergarten', 'university', 'college', 'training', 'courses'])]
leisure = data[
    data['leisure'].isin(['park', 'garden', 'playground', 'stadium', 'sports_centre', 'swimming_pool']) |
    data['tourism'].isin(['museum', 'art_gallery', 'theme_park', 'zoo', 'aquarium']) |
    data['shop'].isin(['mall', 'supermarket', 'department_store'])
]
food = data[data['amenity'].isin(['cafe', 'restaurant', 'food_court', 'fast_food', 'bar', 'pub'])]

# Clean each GeoDataFrame
residence_clean = clean_geodataframe(residence)
office_clean = clean_geodataframe(office)
study_clean = clean_geodataframe(study)
leisure_clean = clean_geodataframe(leisure)
food_clean = clean_geodataframe(food)

# Verify serialization for each category
def verify_serialization(gdf, name):
    try:
        json_str = gdf.to_json()
        json.loads(json_str)
        print(f"{name} GeoDataFrame is JSON serializable.")
    except TypeError as e:
        print(f"Serialization error in {name}: {e}")

verify_serialization(residence_clean, 'Residence Unit')
verify_serialization(office_clean, 'Office and Work Unit')
verify_serialization(study_clean, 'Study Unit')
verify_serialization(leisure_clean, 'Leisure Unit')
verify_serialization(food_clean, 'Food Unit')

# Create the map
map_center = data.geometry.unary_union.centroid.coords[0][::-1]
m = folium.Map(location=map_center, zoom_start=13, tiles='cartodbpositron')

# Function to add GeoDataFrame to map
def add_geodataframe_to_map(gdf, map_object, color, layer_name):
    folium.GeoJson(
        data=gdf,
        style_function=lambda feature: {
            'fillColor': color,
            'color': color,
            'weight': 1,
            'fillOpacity': 0.6,
        },
        tooltip=folium.GeoJsonTooltip(
            fields=['name', 'amenity', 'building', 'shop', 'tourism', 'leisure'],
            aliases=['Name:', 'Amenity:', 'Building:', 'Shop:', 'Tourism:', 'Leisure:'],
            localize=True
        ),
        name=layer_name
    ).add_to(map_object)

# Add each category to the map
add_geodataframe_to_map(residence_clean, m, 'blue', 'Residence Unit')
add_geodataframe_to_map(office_clean, m, 'green', 'Office and Work Unit')
add_geodataframe_to_map(study_clean, m, 'orange', 'Study Unit')
add_geodataframe_to_map(leisure_clean, m, 'purple', 'Leisure Unit')
add_geodataframe_to_map(food_clean, m, 'red', 'Food Unit')

# Add layer control and save the map
folium.LayerControl().add_to(m)
m.save('categorized_map.html')


Residence Unit GeoDataFrame is JSON serializable.
Office and Work Unit GeoDataFrame is JSON serializable.
Study Unit GeoDataFrame is JSON serializable.
Leisure Unit GeoDataFrame is JSON serializable.
Food Unit GeoDataFrame is JSON serializable.


In [3]:
m